In [1]:
from IPython.core.display import display, HTML
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
import datetime as dt
import warnings
warnings.filterwarnings('ignore')
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objs as go
import plotly.express as px
import chart_studio.plotly as py
from plotly.subplots import make_subplots

In [2]:
display(HTML('<h1><center><b>Идентификация модели поведения веб-пользователя методами машинного обучения</b></center></h1>'))

In [3]:
display(HTML('<p><h4><b>Набор данных до обработки:</b></h4></p>'))

In [4]:
data_before_processing = pd.read_csv('150users/user0486.csv')
data_before_processing

user_id            timestamp                        site
0           1  2013-11-19 13:32:51  fpdownload2.macromedia.com
1           1  2013-11-19 13:32:59               www.google.fr
2           1  2013-11-19 13:33:00              www.google.com
3           1  2013-11-19 13:33:00               www.google.fr
4           1  2013-11-19 13:33:00                www.bing.com
...       ...                  ...                         ...
6515        1  2014-03-31 16:45:40              www.google.com
6516        1  2014-03-31 16:45:47               www.google.fr
6517        1  2014-03-31 16:45:48            go.microsoft.com
6518        1  2014-03-31 16:45:48      ieonline.microsoft.com
6519        1  2014-03-31 16:47:53     gtssl-ocsp.geotrust.com

[6520 rows x 3 columns]

In [5]:
display(HTML('<p><h4><b>Набор данных после обработки:</b></h4></p>'))

In [6]:
data_after_processing = pd.read_csv('sessions_with_domains.csv')
times = ['time' + str(i) for i in range(1, 21)]
sites = ['site' + str(i) for i in range(1, 21)]

data_after_processing[times] = data_after_processing[times].apply(pd.to_datetime)
data_after_processing['target'] = data_after_processing['target'].astype('int')
data_after_processing['number_of_sites'] = ((data_after_processing.notna().sum(axis=1)) -1) / 2
data_after_processing['number_of_sites'] = data_after_processing['number_of_sites'].astype('int64')
data_after_processing['session_start'] = data_after_processing[[f"time{i}" for i in range(1,11)]].min(axis=1)
data_after_processing['session_end'] = data_after_processing[[f"time{i}" for i in range(1,11)]].max(axis=1)
data_after_processing['session_duration'] = (data_after_processing['session_end'] - data_after_processing['session_start']).dt.seconds
data_after_processing['minute'] = data_after_processing['session_start'].dt.minute
data_after_processing['hour'] = data_after_processing['session_start'].dt.hour
data_after_processing['hour'] = data_after_processing['hour'].astype('category')
data_after_processing['day'] = data_after_processing['session_start'].dt.day
data_after_processing['day'] = data_after_processing['day'].astype('category')
data_after_processing['weekday'] = data_after_processing['session_start'].dt.dayofweek
data_after_processing['weekday'] = data_after_processing['weekday'].astype('category')
data_after_processing['month'] = data_after_processing['session_start'].dt.month
del data_after_processing['session_start']
del data_after_processing['session_end']
data_after_processing['favourite_hour'] = data_after_processing['hour'].apply(lambda x: (x >= 10) & (x <= 11) | (x >= 13) & (x <= 15)).astype('int')
data_after_processing['favourite_weekday'] = data_after_processing['weekday'].apply(lambda x: (x >= 0) & (x <= 4)).astype('int')
data_after_processing['favourite_day'] = data_after_processing['day'].apply(lambda x: (x == 3) | (x == 5) | (x == 9) | (x == 19) | (x == 26) | (x == 27) | (x == 28) | (x == 31)).astype('int')
data_after_processing['favourite_month'] = data_after_processing['month'].apply(lambda x: (x == 3) | (x == 11) | (x == 12)).astype('int')
data_after_processing

time1                  site1               time2  \
0     2013-11-15 08:01:09          www.google.fr 2013-11-15 08:01:10   
1     2013-11-15 08:04:12        armmf.adobe.com 2013-11-15 08:05:31   
2     2013-11-15 08:06:29          www.google.fr 2013-11-15 08:06:30   
3     2013-11-15 08:07:35         www.google.com 2013-11-15 08:07:35   
4     2013-11-15 08:07:54  www.apogeedigital.com 2013-11-15 08:07:55   
...                   ...                    ...                 ...   
83261 2014-05-28 19:02:25    www.mangareader.net 2014-05-28 19:02:25   
83262 2014-05-28 19:03:03     i5.mangareader.net 2014-05-28 19:03:04   
83263 2014-05-28 19:05:35    www.mangareader.net 2014-05-28 19:05:36   
83264 2014-05-28 19:07:38    www.mangareader.net 2014-05-28 19:07:39   
83265 2014-05-28 19:10:01     i3.mangareader.net 2014-05-28 19:10:14   

                       site2               time3                  site3  \
0              www.google.fr 2013-11-15 08:01:11        apis.google.com   
1              www.google.fr 2013-11-15 08:05:32        apis.google.com   
2              www.google.fr 2013-11-15 08:06:30    ajax.googleapis.com   
3              www.google.fr 2013-11-15 08:07:47          www.google.fr   
4      www.apogeedigital.com 2013-11-15 08:08:00  www.apogeedigital.com   
...                      ...                 ...                    ...   
83261       www.facebook.com 2014-05-28 19:02:51    www.mangareader.net   
83262       www.facebook.com 2014-05-28 19:03:04    www.mangareader.net   
83263       www.facebook.com 2014-05-28 19:05:36    www.mangareader.net   
83264    www.mangareader.net 2014-05-28 19:07:40       www.facebook.com   
83265    www.mangareader.net 2014-05-28 19:10:15       www.facebook.com   

                    time4                  site4               time5  \
0     2013-11-15 08:01:12         www.google.com 2013-11-15 08:01:16   
1     2013-11-15 08:05:32         www.google.com 2013-11-15 08:05:35   
2     2013-11-15 08:06:30   www.sol-solution.com 2013-11-15 08:06:31   
3     2013-11-15 08:07:47        apis.google.com 2013-11-15 08:07:47   
4     2013-11-15 08:08:01  www.apogeedigital.com 2013-11-15 08:08:02   
...                   ...                    ...                 ...   
83261 2014-05-28 19:02:52       www.facebook.com 2014-05-28 19:02:53   
83262 2014-05-28 19:03:50    www.mangareader.net 2014-05-28 19:03:51   
83263 2014-05-28 19:06:01    www.mangareader.net 2014-05-28 19:06:02   
83264 2014-05-28 19:07:46    www.mangareader.net 2014-05-28 19:07:47   
83265 2014-05-28 19:10:15    www.mangareader.net                 NaT   

                       site5  ... session_duration minute hour day weekday  \
0              www.google.fr  ...               57      1    8  15       4   
1              www.google.fr  ...               97      4    8  15       4   
2       www.sol-solution.com  ...               47      6    8  15       4   
3               id.google.fr  ...               32      7    8  15       4   
4      www.apogeedigital.com  ...               12      7    8  15       4   
...                      ...  ...              ...    ...  ...  ..     ...   
83261     i6.mangareader.net  ...               32      2   19  28       2   
83262    www.mangareader.net  ...               65      3   19  28       2   
83263    www.mangareader.net  ...               85      5   19  28       2   
83264    www.mangareader.net  ...               28      7   19  28       2   
83265                    NaN  ...               14     10   19  28       2   

      month favourite_hour favourite_weekday favourite_day favourite_month  
0        11              0                 1             0               1  
1        11              0                 1             0               1  
2        11              0                 1             0               1  
3        11              0                 1             0               1  
4        11              0                 1             0         

In [7]:
display(HTML('<p><h4><b>Диаграммы, характеризующие поведение Элис:</b></h4></p>'))

In [18]:
fig = make_subplots(rows=1, cols=2, start_cell="bottom-left", x_title='Час', y_title='Количество')

fig.append_trace(go.Histogram(x=data_after_processing[data_after_processing.target == 1].hour, name='Элис'),1,1)
fig.append_trace(go.Histogram(x=data_after_processing[data_after_processing.target == 0].hour, name='Другие'),1,2)
fig.update_layout(
    title_text='Час открытия сессии',
    bargroupgap=0.1,
    xaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    xaxis2 = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    height=500,
    width=1200
)
fig.show()

In [9]:
fig = make_subplots(rows=1, cols=2, start_cell="bottom-left", x_title='День недели', y_title='Количество')

fig.append_trace(go.Histogram(x=data_after_processing[data_after_processing.target == 1].weekday, name='Элис'),1,1)
fig.append_trace(go.Histogram(x=data_after_processing[data_after_processing.target == 0].weekday, name='Другие'),1,2)
fig.update_layout(
    title_text='День недели открытия сессии',
    bargroupgap=0.1,
    xaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    xaxis2 = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    height=500,
    width=1200
)
fig.show()

In [128]:
fig = make_subplots(rows=1, cols=2, start_cell="bottom-left", x_title='День', y_title='Количество')

fig.append_trace(go.Histogram(x=data_after_processing[data_after_processing.target == 1].day, name='Элис'),1,1)
fig.append_trace(go.Histogram(x=data_after_processing[data_after_processing.target == 0].day, name='Другие'),1,2)
fig.update_layout(
    title_text='День открытия сессии',
    bargroupgap=0.1,
    xaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    xaxis2 = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    height=500,
    width=1200
)
fig.show()

In [129]:
fig = make_subplots(rows=1, cols=2, start_cell="bottom-left", x_title='Месяц', y_title='Количество')

fig.append_trace(go.Histogram(x=data_after_processing[data_after_processing.target == 1].month, name='Элис'),1,1)
fig.append_trace(go.Histogram(x=data_after_processing[data_after_processing.target == 0].month, name='Другие'),1,2)
fig.update_layout(
    title_text='Месяц открытия сессии',
    bargroupgap=0.1,
    xaxis = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    xaxis2 = dict(
        tickmode = 'linear',
        tick0 = 0,
        dtick = 1
    ),
    height=500,
    width=1200
)
fig.show()

In [28]:
display(HTML('<p><h4><b>Оценка качества моделей первого набора данных:</b></h4></p>'))

In [27]:
data = [
     ['Логистическая регрессия', 0.96, 0.99, 0.28, 0.75, 0.4, 0.45, '3 min 24 s'],
     ['Градиентный бустинг', 0.78, 0.99, 0.22, 0.41, 0.29, 0.3, '6 min 34 s'],
     ['Адаптивный бустинг', 0.91, 0.99, 0.16, 0.9, 0.28, 0.38, '3 min 4 s'],
     ['Дерево решений', 0.62, 0.99, 0.19, 0.27, 0.22, 0.23, '8 s'],
     ['Случайный лес', 0.91, 0.99, 0.09, 0.9, 0.16, 0.29, '10 min 12 s'],
     ['Метод опорных векторов', 0.53, 0.99, 0.06, 0.87, 0.12, 0.23, '21 min 3 s'],
]
df = pd.DataFrame(data, columns=['Алгоритм', 'ROC-AUC', 'Accuracy', 'Recall', 'Precision', 'F1-score', 'Phi coefficient', 'Время обучения'])
df

Алгоритм  ROC-AUC  Accuracy  Recall  Precision  F1-score  \
0  Логистическая регрессия     0.96      0.99    0.28       0.75      0.40   
1      Градиентный бустинг     0.78      0.99    0.22       0.41      0.29   
2       Адаптивный бустинг     0.91      0.99    0.16       0.90      0.28   
3           Дерево решений     0.62      0.99    0.19       0.27      0.22   
4            Случайный лес     0.91      0.99    0.09       0.90      0.16   
5   Метод опорных векторов     0.53      0.99    0.06       0.87      0.12   

   Phi coefficient Время обучения  
0             0.45     3 min 24 s  
1             0.30     6 min 34 s  
2             0.38      3 min 4 s  
3             0.23            8 s  
4             0.29    10 min 12 s  
5             0.23     21 min 3 s

In [29]:
display(HTML('<p><h4><b>Оценка качества моделей второго набора данных:</b></h4></p>'))

In [32]:
data = [
     ['Логистическая регрессия', 0.99, 0.99, 0.59, 0.87, 0.71, 0.72, '16 min 13 s'],
     ['Градиентный бустинг', 0.97, 0.99, 0.4, 0.76, 0.52, 0.55, '7 min 11 s'],
     ['Адаптивный бустинг', 0.99, 0.99, 0.41, 0.75, 0.53, 0.55, '3 min 8 s'],
     ['Дерево решений', 0.65, 0.99, 0.3, 0.32, 0.31, 0.31, '5 s'],
     ['Случайный лес', 0.96, 0.99, 0.15, 0.94, 0.27, 0.38, '6 min 32 s'],
     ['Метод опорных векторов', 0.99, 0.99, 0.46, 0.94, 0.62, 0.66, '6 min 52 s'],
]
df = pd.DataFrame(data, columns=['Алгоритм', 'ROC-AUC', 'Accuracy', 'Recall', 'Precision', 'F1-score', 'Phi coefficient', 'Время обучения'])
df

Алгоритм  ROC-AUC  Accuracy  Recall  Precision  F1-score  \
0  Логистическая регрессия     0.99      0.99    0.59       0.87      0.71   
1      Градиентный бустинг     0.97      0.99    0.40       0.76      0.52   
2       Адаптивный бустинг     0.99      0.99    0.41       0.75      0.53   
3           Дерево решений     0.65      0.99    0.30       0.32      0.31   
4            Случайный лес     0.96      0.99    0.15       0.94      0.27   
5   Метод опорных векторов     0.99      0.99    0.46       0.94      0.62   

   Phi coefficient Время обучения  
0             0.72    16 min 13 s  
1             0.55     7 min 11 s  
2             0.55      3 min 8 s  
3             0.31            5 s  
4             0.38     6 min 32 s  
5             0.66     6 min 52 s

In [30]:
display(HTML('<p><h4><b>Оценка качества моделей третьего набора данных:</b></h4></p>'))

In [33]:
data = [
     ['Логистическая регрессия', 0.99, 0.99, 0.57, 0.84, 0.68, 0.69, '16 min 55 s'],
     ['Градиентный бустинг', 0.79, 0.99, 0.49, 0.64, 0.56, 0.56, '6 min 40 s'],
     ['Адаптивный бустинг', 0.98, 0.99, 0.38, 0.85, 0.52, 0.57, '4 min 17 s'],
     ['Дерево решений', 0.63, 0.99, 0.22, 0.31, 0.26, 0.26, '7 s'],
     ['Случайный лес', 0.95, 0.99, 0.15, 1, 0.27, 0.39, '7 min 21 s'],
     ['Метод опорных векторов', 0.99, 0.99, 0.51, 0.94, 0.66, 0.69, '9 min 53 s'],
]
df = pd.DataFrame(data, columns=['Алгоритм', 'ROC-AUC', 'Accuracy', 'Recall', 'Precision', 'F1-score', 'Phi coefficient', 'Время обучения'])
df

Алгоритм  ROC-AUC  Accuracy  Recall  Precision  F1-score  \
0  Логистическая регрессия     0.99      0.99    0.57       0.84      0.68   
1      Градиентный бустинг     0.79      0.99    0.49       0.64      0.56   
2       Адаптивный бустинг     0.98      0.99    0.38       0.85      0.52   
3           Дерево решений     0.63      0.99    0.22       0.31      0.26   
4            Случайный лес     0.95      0.99    0.15       1.00      0.27   
5   Метод опорных векторов     0.99      0.99    0.51       0.94      0.66   

   Phi coefficient Время обучения  
0             0.69    16 min 55 s  
1             0.56     6 min 40 s  
2             0.57     4 min 17 s  
3             0.26            7 s  
4             0.39     7 min 21 s  
5             0.69     9 min 53 s

In [31]:
display(HTML('<p><h4><b>Оценка качества моделей четвертого набора данных:</b></h4></p>'))

In [34]:
data = [
     ['Логистическая регрессия', 0.99, 0.99, 0.56, 0.84, 0.67, 0.68, '10 min 52 s'],
     ['Градиентный бустинг', 0.96, 0.99, 0.42, 0.62, 0.5, 0.51, '6 min 49 s'],
     ['Адаптивный бустинг', 0.98, 0.99, 0.35, 0.84, 0.5, 0.54, '3 min 5 s'],
     ['Дерево решений', 0.64, 0.99, 0.27, 0.41, 0.32, 0.33, '7 s'],
     ['Случайный лес', 0.95, 0.99, 0.16, 0.94, 0.28, 0.39, '7 min 35 s'],
     ['Метод опорных векторов', 0.98, 0.99, 0.44, 0.9, 0.6, 0.33, '7 min 26 s'],
]
df = pd.DataFrame(data, columns=['Алгоритм', 'ROC-AUC', 'Accuracy', 'Recall', 'Precision', 'F1-score', 'Phi coefficient', 'Время обучения'])
df

Алгоритм  ROC-AUC  Accuracy  Recall  Precision  F1-score  \
0  Логистическая регрессия     0.99      0.99    0.56       0.84      0.67   
1      Градиентный бустинг     0.96      0.99    0.42       0.62      0.50   
2       Адаптивный бустинг     0.98      0.99    0.35       0.84      0.50   
3           Дерево решений     0.64      0.99    0.27       0.41      0.32   
4            Случайный лес     0.95      0.99    0.16       0.94      0.28   
5   Метод опорных векторов     0.98      0.99    0.44       0.90      0.60   

   Phi coefficient Время обучения  
0             0.68    10 min 52 s  
1             0.51     6 min 49 s  
2             0.54      3 min 5 s  
3             0.33            7 s  
4             0.39     7 min 35 s  
5             0.33     7 min 26 s